In [0]:
%run ./conf_notebook

Import the data

In [0]:
df_train = ps.read_csv(train_3_csv_file_path)
df_train = df_train.drop('_c0', axis=1)

path name size modificationTime dbfs:/mnt/pqsashrd/data/ann_pred_1.csv/ ann_pred_1.csv/ 0 0 dbfs:/mnt/pqsashrd/data/ann_pred_1_test.csv/ ann_pred_1_test.csv/ 0 0 dbfs:/mnt/pqsashrd/data/ann_pred_3.csv/ ann_pred_3.csv/ 0 0 dbfs:/mnt/pqsashrd/data/clust_pred_1.csv/ clust_pred_1.csv/ 0 0 dbfs:/mnt/pqsashrd/data/clust_pred_1_test.csv/ clust_pred_1_test.csv/ 0 0 dbfs:/mnt/pqsashrd/data/clust_pred_3.csv/ clust_pred_3.csv/ 0 0 dbfs:/mnt/pqsashrd/data/clust_pred_3_test.csv/ clust_pred_3_test.csv/ 0 0 dbfs:/mnt/pqsashrd/data/test_1.csv test_1.csv 38574669 1714569841000 dbfs:/mnt/pqsashrd/data/test_2.csv test_2.csv 35056701 1714569835000 dbfs:/mnt/pqsashrd/data/test_3.csv test_3.csv 25575183 1714569796000 dbfs:/mnt/pqsashrd/data/train_1.csv train_1.csv 81417863 1714569888000 dbfs:/mnt/pqsashrd/data/train_1_partitioned/ train_1_partitioned/ 0 0 dbfs:/mnt/pqsashrd/data/train_2.csv train_2.csv 73764410 1714569886000 dbfs:/mnt/pqsashrd/data/train_3.csv train_3.csv 54130409 1714569868000 dbfs:/mnt/pqsashrd/data/train_3_partitioned/ train_3_partitioned/ 0 0

In [0]:
label_encoder = LabelEncoder()
df_train = df_train.to_pandas()
df_train["attack_cat_encoded"] = label_encoder.fit_transform(df_train["attack_cat"])
df_train = ps.DataFrame(df_train)

In [0]:
X_train = df_train.set_index("attack_cat")
X_train = X_train.drop("attack_cat_encoded", axis=1)
y_train = df_train["attack_cat_encoded"]

Adjusted Rand Index (ARI): This metric measures the similarity between two clusterings by considering all pairs of samples and counting pairs that are assigned in the same or different clusters in the predicted and true clusterings. The ARI is adjusted for chance, which makes it more robust for comparing different clustering algorithms.

Silhouette Coefficient: This metric measures how similar an object is to its own cluster (cohesion) compared to other clusters (separation). The Silhouette Coefficient is calculated for each sample and can range from -1 to +1, where a high value indicates that the object is well matched to its own cluster and poorly matched to neighboring clusters. If most objects have a high value, the clustering configuration is appropriate.

### hdbscan

In [0]:
estimator = LDA(n_components = 2)
X_lda = estimator.fit_transform(ps.DataFrame(X_train).to_pandas(), y_train.to_pandas())
X_lda_df = ps.DataFrame(data=X_lda, columns=['LDA_component_1', 'LDA_component_2'], index=ps.DataFrame(X_train).index)
X_lda_df = X_lda_df.to_pandas()

In [0]:
custom_color_scale = [
    '#800080',  # Purple (no change)
    '#9370db',  # Medium Purple (no change)
    '#6495ed',  # Cornflower Blue (no change)
    '#000080',  # Navy (no change)
    '#6998b3',  # Darker Light Blue (no change)
    "#e4cbd1",  # Medium Violet Red (a darker, more subdued pink)
]

In [0]:
estimator = LDA(n_components = 4)
X_lda = estimator.fit_transform(X_train.to_pandas(), y_train.to_pandas())
X_lda_df_ = ps.DataFrame(data=X_lda, columns=['LDA_component_1', 'LDA_component_2', 'LDA_component_3', 'LDA_component_4'], index=X_train.index)
X_lda_df_ = X_lda_df_.to_pandas()

In [0]:
min_cluster_sizes = [15000]  
min_samples_values = [25, 50, 100, 150, 200] 

In [0]:
for min_cluster_size in min_cluster_sizes:
    for min_samples in min_samples_values:
        print(min_cluster_size, min_samples)
        hdbscan_model = hdbscan.HDBSCAN(min_cluster_size=min_cluster_size, min_samples=min_samples)

        hdbscan_model.fit(X_lda_df_)

        cluster_labels = hdbscan_model.labels_
        n_clusters = len(set(cluster_labels)) - (1 if -1 in cluster_labels else 0)
        n_noise = list(cluster_labels).count(-1)

        print(n_clusters, n_noise, X_lda_df_.shape[0])

        predicted_labels = cluster_labels
        true_labels = y_train.to_numpy()

        ari = metrics.adjusted_rand_score(true_labels, predicted_labels)

        spark_df = spark.createDataFrame([(Vectors.dense(x), int(l)) for x, l in zip(X_lda_df_.values, predicted_labels)], ["features", "prediction"])
        evaluator = ClusteringEvaluator(predictionCol='prediction', featuresCol='features', metricName='silhouette', distanceMeasure='squaredEuclidean')
        silhouette_score = evaluator.evaluate(spark_df)

        print(f"Number of clusters = {n_clusters+1}: Silhouette Coefficient = {silhouette_score}, Adjusted Rand Index (ARI) = {ari}")

15000 25
4 21088 175341
Number of clusters = 5: Silhouette Coefficient = 0.76875516111466, Adjusted Rand Index (ARI) = 0.5682166733975911
15000 50
5 4231 175341
Number of clusters = 6: Silhouette Coefficient = 0.8093562912700897, Adjusted Rand Index (ARI) = 0.5601675283435663
15000 100
5 4417 175341
Number of clusters = 6: Silhouette Coefficient = 0.8081561773674083, Adjusted Rand Index (ARI) = 0.5595975974088608
15000 150
5 4633 175341
Number of clusters = 6: Silhouette Coefficient = 0.8115040958162794, Adjusted Rand Index (ARI) = 0.5580147083207653
15000 200
4 5232 175341
Number of clusters = 5: Silhouette Coefficient = 0.6268310824288477, Adjusted Rand Index (ARI) = 0.49643207829617836


In [0]:
min_cluster_size=15000
min_samples=50
hdbscan_model = hdbscan.HDBSCAN(min_cluster_size=min_cluster_size, min_samples=min_samples, prediction_data=True).fit(X_lda_df_)

cluster_labels = hdbscan_model.labels_
n_clusters = len(set(cluster_labels)) - (1 if -1 in cluster_labels else 0)
n_noise = list(cluster_labels).count(-1)

print(n_clusters, n_noise, X_lda_df_.shape[0])

predicted_labels = cluster_labels
true_labels = y_train.to_numpy()

ari = metrics.adjusted_rand_score(true_labels, predicted_labels)

spark_df = spark.createDataFrame([(Vectors.dense(x), int(l)) for x, l in zip(X_lda_df_.values, predicted_labels)], ["features", "prediction"])
evaluator = ClusteringEvaluator(predictionCol='prediction', featuresCol='features', metricName='silhouette', distanceMeasure='squaredEuclidean')
silhouette_score = evaluator.evaluate(spark_df)

print(f"Number of clusters = {n_clusters}: Silhouette Coefficient = {silhouette_score}, Adjusted Rand Index (ARI) = {ari}")

5 4231 175341
Number of clusters = 5: Silhouette Coefficient = 0.8093562912700897, Adjusted Rand Index (ARI) = 0.5601675283435663


In [0]:
single_prob = hdbscan_model.probabilities_  # Get membership functions
soft_clusters = hdbscan.all_points_membership_vectors(hdbscan_model)  # Get membership functions

IOStream.flush timed out
IOStream.flush timed out


In [0]:
soft_clusters_ = ps.DataFrame(soft_clusters, index=X_lda_df.index)
soft_clusters_ = soft_clusters_.to_pandas()

In [0]:
X_lda_df["pred"] = predicted_labels
X_lda_df["prob_pred"] = single_prob

In [0]:
X_lda_df_prova = pd.concat([X_lda_df, soft_clusters_], axis=1)

In [0]:
soft_clusters[0]

array([0.01866733, 0.01581851, 0.01339125, 0.01553808, 0.02804613])

In [0]:
X_lda_df_prova

LDA_component_1  LDA_component_2  ...         3         4
attack_cat                                    ...                    
Normal             0.379744        -1.503430  ...  0.015538  0.028046
Normal             1.060302        -3.170815  ...  0.144907  0.273335
Normal             1.172618        -2.790150  ...  0.137147  0.258388
Normal             0.828251        -3.148528  ...  0.141464  0.286988
Normal             0.479539        -0.925099  ...  0.138991  0.366271
...                     ...              ...  ...       ...       ...
Generic           -2.906454         1.342791  ...  0.212360  0.091845
Shellcode          0.451045        -1.040992  ...  0.085507  0.147999
Generic           -2.906454         1.342791  ...  0.198052  0.117444
Generic           -2.906454         1.342791  ...  0.204844  0.136153
Generic           -2.906454         1.342791  ...  0.168509  0.089703

[175341 rows x 9 columns]

In [0]:
fig = px.scatter(X_lda_df, x='LDA_component_1', y='LDA_component_2', color=X_lda_df["pred"], color_continuous_scale=custom_color_scale)
fig.update_layout(
    title='LDA Scatter Plot in 2D',
    scene = dict(
        xaxis_title='LDA Component 1',
        yaxis_title='LDA Component 2',
    ),
    legend_title='Attack category',
    width=800,
    height=600
)
fig.show()